# Validiting predictions

In [51]:
import pandas as pd
import folium
from folium.plugins import HeatMap


json_file = 'data/45000_points_geolocation_ids.json' 

data_points = pd.read_json(json_file, orient='index').reset_index(drop=True)


print(data_points.head())  


csv_file = '/data/group_inclusivity.csv' 
scores = pd.read_csv(csv_file)


scores.rename(columns={'Group Inclusivity': 'prediction_score'}, inplace=True)

merged_data = pd.merge(data_points, scores, on='point_id')

print(merged_data.head()) 



    latitude  longitude          point_id
0  45.454712 -73.413522  1337753813784982
1  45.444822 -73.665072  1352499262142437
2  45.416290 -73.614225  1352908008579229
3  45.427001 -73.491413  1386498345284695
4  45.464915 -73.823364  1389592961634400
    latitude  longitude          point_id  prediction_score
0  45.454712 -73.413522  1337753813784982          1.986231
1  45.444822 -73.665072  1352499262142437          2.063999
2  45.416290 -73.614225  1352908008579229          1.035953
3  45.427001 -73.491413  1386498345284695          1.651430
4  45.464915 -73.823364  1389592961634400          2.006349


# Group Inclusivity

In [2]:
import folium
from folium.plugins import HeatMap
import pandas as pd
import branca.colormap as cm

json_file = 'data/45000_points_geolocation_ids.jsonn'
data_points = pd.read_json(json_file, orient='index').reset_index(drop=True)

csv_file = '/data/group_inclusivity.csv'
scores = pd.read_csv(csv_file)
scores.rename(columns={'Group Inclusivity': 'prediction_score'}, inplace=True)


merged_data = pd.merge(data_points, scores, on='point_id')


m = folium.Map(location=[45.5017, -73.5673], zoom_start=13, tiles='cartodbdark_matter')


merged_data['normalized_score'] = (merged_data['prediction_score'] - 1) / 3


gradient = {
    0: '#FF8C00',  # Orange for exclusive
    0.1: '#FF8C00',  # Orange for exclusive
    0.2: '#FF8C00',  # Orange for exclusive
    0.3: '#FF8C00',  # Orange for exclusive
    0.4: '#FF8C00',  # Orange for exclusive
    0.5: '#0000FF',  # Blue for intermediate
    0.6: '#0000FF',  # Blue for intermediate
    0.7: '#0000FF',  # Blue for intermediate
    0.8: '#FFFFFF',  # White for inclusive
    0.9: '#FFFFFF',  # White for inclusive
    1: '#FFFFFF'    # White for inclusive
}


heat_data = [[row['latitude'], row['longitude'], row['normalized_score']] for index, row in merged_data.iterrows()]
HeatMap(heat_data, radius=8, min_opacity=0.4, max_opacity=0.8, gradient=gradient).add_to(m)


linear = cm.LinearColormap(
    ['#FF8C00', '#0000FF', '#FFFFFF'],
    vmin=0, vmax=1,  
    caption='Inclusivity Scale'  
).add_to(m)  

legend_html = '''
<div style="position: fixed; 
            top: 50px; right: 30px; width: 140px; height: 70px; 
            border:2px solid grey; z-index:9999; font-size:10px;
            background-color: rgba(0,0,0,0.8); color: white;">
    &nbsp; <b style="font-size: 11px;">Group Inclusivity</b><br>
    &nbsp; Orange: Exclusive<br>
    &nbsp; Blue: Intermediate<br>
    &nbsp; White: Inclusive
</div>
'''


m.get_root().html.add_child(folium.Element(legend_html))

m.save('/montreal_folium_heatmap_group_inclusivity.html')


m


In [1]:
import folium
from folium.plugins import HeatMap
import pandas as pd
from branca.colormap import LinearColormap

# Load your data
json_file = '/Users/rsdmu/Desktop/mac-tiny/public-I/0_source_data/geolocation_ids.json'
data_points = pd.read_json(json_file, orient='index').reset_index(drop=True)

csv_file = '/Users/rsdmu/Desktop/mac-tiny/public-I/0_source_data/inclusivity.csv'  # Adjusted for group inclusivity data
scores = pd.read_csv(csv_file)
scores.rename(columns={'Group Inclusivity': 'prediction_score'}, inplace=True)  # Updated column name

# Merge datasets on 'point_id'
merged_data = pd.merge(data_points, scores, on='point_id')

# Initialize a map centered around the location
m = folium.Map(location=[45.5017, -73.5673], zoom_start=13, tiles='cartodbpositron')  # White base map

# Normalize the prediction scores to a 0-1 scale
merged_data['normalized_score'] = (merged_data['prediction_score'] - 1) / 3

# Define a highly granular gradient: Black -> Blue -> Green
gradient = {
    "0.0": '#000000',  # Black
    "0.1": '#000022',  # Very dark navy
    "0.2": '#000066',  # Dark navy blue
    "0.3": '#000066',  # Navy blue
    "0.4": '#000066',  # Deep blue
    "0.5": '#0000FF',  # Medium blue
    "0.6": '#66FF66',  # light green 
    "0.7": '#66FF66',  # Light green
    "0.8": '#66FF66',  # Lime green
    "0.9": '#99FF99',  # Pale green
    "1.0": '#00FF00'   # Bright green
}

# Create a HeatMap
heat_data = [[row['latitude'], row['longitude'], row['normalized_score']] for index, row in merged_data.iterrows()]
HeatMap(heat_data, radius=9, min_opacity=0.4, max_opacity=0.9, gradient=gradient).add_to(m)

# Add a gradient bar to represent the color scale
colormap = LinearColormap(
    colors=['#000000', '#000022', '#000044', '#000066', '#000066', '#0000FF', '#0055FF', '#33CC33', '#66FF66', '#99FF99', '#00FF00'],  # Smooth transition
    vmin=0, vmax=1,  # Range for normalized score
    caption='Inclusivity Scale'  # Updated caption
)
colormap.add_to(m)

# Define a custom HTML legend
legend_html = '''
<div style="position: fixed; 
            top: 50px; right: 30px; width: 220px; height: 80px; 
            border:2px solid grey; z-index:9999; font-size:12px;
            background-color: rgba(255, 255, 255, 0.9); color: black; padding: 10px;">
    <b> Inclusivity: Group Evaluation</b><br>
    <span style="color: #000000;">&#9632;</span> Black: Exclusive<br>
    <span style="color: #00FF00;">&#9632;</span> Bright Green: Inclusive
</div>
'''

# Add the custom legend to the map
m.get_root().html.add_child(folium.Element(legend_html))

# Save the map to an HTML file
m.save('/Users/rsdmu/Desktop/figs/montreal_folium_heatmap_group_inclusivity.html')

# Display the map in a Jupyter Notebook (if applicable)
m


In [2]:
import folium
from folium.plugins import HeatMap
import pandas as pd
from branca.colormap import LinearColormap

# Load your data
json_file = '/Users/rsdmu/Desktop/mac-tiny/public-I/0_source_data/geolocation_ids.json'
data_points = pd.read_json(json_file, orient='index').reset_index(drop=True)

csv_file = '/Users/rsdmu/Desktop/mac-tiny/public-I/0_source_data/handicapped_inclusivity.csv'
scores = pd.read_csv(csv_file)
scores.rename(columns={'Handicapped Inclusivity': 'prediction_score'}, inplace=True)


# Merge datasets on 'point_id'
merged_data = pd.merge(data_points, scores, on='point_id')

# Initialize a map centered around the location
m = folium.Map(location=[45.5017, -73.5673], zoom_start=12.5, tiles='cartodbpositron')  # White base map

# Normalize the prediction scores to a 0-1 scale
merged_data['normalized_score'] = (merged_data['prediction_score'] - 1) / 3

# Define a highly granular gradient: Black -> Blue -> Green
gradient = {
    "0.0": '#000000',  # Black
    "0.1": '#000022',  # Very dark navy
    "0.2": '#000066',  # Dark navy blue
    "0.3": '#000066',  # Navy blue
    "0.4": '#000066',  # Deep blue
    "0.5": '#0000FF',  # Medium blue
    "0.6": '#66FF66',  # light green 
    "0.7": '#66FF66',  # Light green
    "0.8": '#66FF66',  # Lime green
    "0.9": '#99FF99',  # Pale green
    "1.0": '#00FF00'   # Bright green
}

# Create a HeatMap
heat_data = [[row['latitude'], row['longitude'], row['normalized_score']] for index, row in merged_data.iterrows()]
HeatMap(heat_data, radius=9, min_opacity=0.4, max_opacity=0.9, gradient=gradient).add_to(m)

# Add a gradient bar to represent the color scale
colormap = LinearColormap(
    colors=['#000000', '#000022', '#000044', '#000066', '#000066', '#0000FF', '#0055FF', '#33CC33', '#66FF66', '#99FF99', '#00FF00'],  # Smooth transition
    vmin=0, vmax=1,  # Range for normalized score
    caption='Inclusivity Scale'  # Updated caption
)
colormap.add_to(m)

# Define a custom HTML legend
legend_html = '''
<div style="position: fixed; 
            top: 50px; right: 30px; width: 220px; height: 80px; 
            border:2px solid grey; z-index:9999; font-size:12px;
            background-color: rgba(255, 255, 255, 0.9); color: black; padding: 10px;">
    <b>Inclusivity: Handicap Evaluation</b><br>
    <span style="color: #000000;">&#9632;</span> Black: Exclusive<br>
    <span style="color: #00FF00;">&#9632;</span> Bright Green: Inclusive
</div>
'''

# Add the custom legend to the map
m.get_root().html.add_child(folium.Element(legend_html))



# Save the map to an HTML file
m.save('/Users/rsdmu/Desktop/figs/montreal_folium_heatmap_handicapped_inclusivity.html')

# Display the map in a Jupyter Notebook (if applicable)
m
